In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np
import folium
import json, requests

In [2]:
with open('../data/USA-county.txt', 'r') as us_county_file:

    county_txt_data = us_county_file.readlines()

In [3]:
def parse_coordinates(coords):
    """INPUT: coords - a list of strings of coordinates
    OUTPUT: A list of tuples of coordinates"""
    to_float = lambda x: float(x)
    
    return [[list(map(to_float, elem.strip().split())) for elem in coords]]

In [4]:
contiguous_us_bounds = parse_coordinates(county_txt_data[0:2])
counties_remaining = int(county_txt_data[2].strip())

ii = 3

counties_list = []

while ii < len(county_txt_data):
    county_dict = {'type':'Feature'}
    
    if len(county_txt_data[ii].strip()) == 0:   # skip the blank lines
        ii += 1
        if ii == len(county_txt_data):
            break
    
    county_name = county_txt_data[ii].strip()
    ii += 1
    state_abbr = county_txt_data[ii].strip()
    ii += 1
    
    county_dict['properties'] = {'name':county_name, 'state':state_abbr}
    
    num_of_coords = int(county_txt_data[ii].strip())
    ii += 1
    county_coords = parse_coordinates(county_txt_data[ii:ii+num_of_coords])
    ii += num_of_coords
    
    county_dict['geometry'] = {'type':'Polygon', 'coordinates':county_coords}
    
    counties_list.append(county_dict)
    
    counties_remaining -= 1

In [5]:
print(county_name)
print(state_abbr)
print(num_of_coords)
print(len(county_coords[0]), '\n', county_coords)

Weston
WY
11
11 
 [[[-105.078743, 44.176205], [-104.375, 44.181641], [-104.054001, 44.180401], [-104.054108, 44.141102], [-104.055, 43.8535], [-104.054298, 43.503101], [-104.899414, 43.499668], [-105.079262, 43.498474], [-105.081238, 43.592144], [-105.078255, 43.827049], [-105.080872, 43.826954]]]


In [6]:
my_geo_counties = {'type': 'FeatureCollection',
                   'features':counties_list}

In [7]:
m = folium.Map([46, -93], tiles='cartodbpositron', zoom_start=7)

def add_district_to_map(district_data):
    folium.GeoJson(
        district_data,
        style_function=lambda feature: {
#             'fillColor' : district_data['features'][0]['fillColor'],
            'fillColor': 'green',
            'color':'grey',
            'weight': 1,
            'dashArray': '1, 5'
        }
    ).add_to(m)

In [8]:
add_district_to_map(my_geo_counties)

m